In [2]:
import numpy as np
import pandas as pd
import altair as alt

In [61]:
# load in data
opioid_deaths = pd.read_parquet("/Users/yangshining/Desktop/pds2021-opioids-pds6/10_modified_data/vital_pop.parquet", engine='fastparquet')
opioid_buyers = pd.read_parquet("/Users/yangshining/Desktop/pds2021-opioids-pds6/10_modified_data/opi_pop.parquet", engine='fastparquet')

In [62]:
opioid_buyers=opioid_buyers.rename(columns={"MME per cap":"MME_per_cap"})
opioid_deaths=opioid_deaths.rename(columns={"vital deaths per cap":"deaths_per_cap"})
opioid_buyers.sample(10)

BUYER_STATE BUYER_COUNTY   fips  year           MME  Population  \
index                                                                   
735            FL        DUVAL  12031  2012  5.553281e+08    880108.0   
1566           GA      DECATUR  13087  2008  7.571151e+06     28010.0   
5332           OK     MARSHALL  40095  2013  6.776548e+06     16065.0   
3379           LA  ST. TAMMANY  22103  2007  1.281662e+08    226294.0   
5743           OR   HOOD RIVER  41027  2010  6.696308e+06     22346.0   
7384           TX      KAUFMAN  48257  2009  3.091049e+07    101709.0   
7850           TX       POTTER  48375  2014  3.112886e+07    122061.0   
2094           GA   MONTGOMERY  13209  2011  4.035963e+05      9030.0   
7490           TX          LEE  48287  2007  1.860983e+06     16421.0   
7074           TX         GRAY  48179  2014  6.783640e+06     23432.0   

       MME_per_cap  treatment  
index                          
735     630.977198          1  
1566    270.301711          0  
5332    421.820604          0  
3379    566.370116          0  
5743    299.664717          0  
7384    303.911102          0  
7850    255.027117          0  
2094     44.695050          0  
7490    113.329454          0  
7074    289.503229          0

In [4]:
opioid_buyers['year'].unique()

array([2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014], dtype=int64)

In [5]:
opioid_deaths['Year'].unique()

array([2003, 2005, 2006, 2007, 2009, 2010, 2011, 2004, 2008, 2012, 2013,
       2014, 2015], dtype=int64)

In [63]:
## Nick's code for confidence bands 
def get_reg_fit(data, yvar, xvar, alpha=0.05,col="blue"):
    import statsmodels.formula.api as smf

    # Grid for predicted values
    x = data.loc[pd.notnull(data[yvar]), xvar]
    xmin = x.min()
    xmax = x.max()
    step = (xmax - xmin) / 100
    grid = np.arange(xmin, xmax + step, step)
    predictions = pd.DataFrame({xvar: grid})

    # Fit model, get predictions
    model = smf.ols(f"{yvar} ~ {xvar}", data=data).fit()
    model_predict = model.get_prediction(predictions[xvar])
    predictions[yvar] = model_predict.summary_frame()["mean"]
    predictions[["ci_low", "ci_high"]] = model_predict.conf_int(alpha=alpha)

    # Build chart
    reg = alt.Chart(predictions).mark_line(color=col).encode(
        x=alt.X(xvar, axis=alt.Axis(title='Years from Policy Change')),
        y=alt.X(yvar, axis=alt.Axis(title='')))
    ci = (
        alt.Chart(predictions)
        .mark_errorband(color=col)
        .encode(
            x=xvar,
            y=alt.Y("ci_low", title=""),
            y2="ci_high",
        )
    )
    chart = ci + reg
    return predictions, chart

# Florida plots

In [64]:
# Creating florida buyers df
states = ["SC","AL","GA","MS", "FL"]
opioid_buyers_fl=opioid_buyers[opioid_buyers["BUYER_STATE"].isin(states)]

#create column, to indicate whether control or not (1 for control, 0 for florida)
opioid_buyers_fl["is_control"]=np.where(opioid_buyers_fl["BUYER_STATE"]== 'FL', 0, 1)

#create policy years 
opioid_buyers_fl["policy_years"]= opioid_buyers_fl["year"]-2010
fl_opi_before=opioid_buyers_fl[opioid_buyers_fl["policy_years"]<0]
fl_opi_after=opioid_buyers_fl[opioid_buyers_fl["policy_years"]>=0]

/var/folders/g3/gw7r7tvj63j5wjhsmmnq03qr0000gn/T/ipykernel_39162/3804853719.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opioid_buyers_fl["is_control"]=np.where(opioid_buyers_fl["BUYER_STATE"]== 'FL', 0, 1)
/var/folders/g3/gw7r7tvj63j5wjhsmmnq03qr0000gn/T/ipykernel_39162/3804853719.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opioid_buyers_fl["policy_years"]= opioid_buyers_fl["year"]-2010


In [65]:
#create vertical line for plots
data = pd.DataFrame({"a": [0]})
sep_line = (alt.Chart(data).mark_rule(color="black", strokeDash=[10, 10]).encode(x=alt.X("a:Q", title="")))

In [68]:
# florida buyers pre/post plot
# Stuffs for making legends
legend = alt.Chart(fl_opi_before).transform_calculate(fl= "'Florida'", control="'control'")
scale = alt.Scale(domain=["Florida", "Control"], range=['red', 'blue'])

before = alt.Chart(
    fl_opi_before, title="Pre-Post Policy: Florida, Opioids per cap"
).encode(x="policy_years", y=alt.Y("MME_per_cap", title="Opioids per Cap", scale=alt.Scale(zero=False)), color=alt.Color('fl:N', scale=scale, title=''))

base = before.transform_regression("policy_years", "MME_per_cap").mark_line()


after = alt.Chart(
    fl_opi_after, title="Pre-Post Policy: Florida, Opioids per cap"
).encode(x="policy_years", y="MME_per_cap", color=alt.Color('control:N', scale=scale, title=''))

base2 = after.transform_regression("policy_years", "MME_per_cap").mark_line()

fit, before_line = get_reg_fit(
    fl_opi_before[fl_opi_before["is_control"] == 1],
    yvar="MME_per_cap",
    xvar="policy_years",
    alpha=0.05,
    col="blue",
)
fit, before_line2 = get_reg_fit(
    fl_opi_before[fl_opi_before["is_control"] == 0],
    yvar="MME_per_cap",
    xvar="policy_years",
    alpha=0.05,
    col="red"
)
fit, after_line = get_reg_fit(
    fl_opi_after[fl_opi_after["is_control"] == 1],
    yvar="MME_per_cap",
    xvar="policy_years",
    alpha=0.05,
    col="blue",
)
fit, after_line2 = get_reg_fit(
    fl_opi_after[fl_opi_after["is_control"] == 0],
    yvar="MME_per_cap",
    xvar="policy_years",
    alpha=0.05,
    col="red"
)

fl_pre_post = base + before_line2 + after_line2 +sep_line
fl_pre_post

alt.LayerChart(...)

In [70]:
# diff-in-diff
before = alt.Chart(
    fl_opi_before, title="Difference in Difference: Florida vs. Control, Opioids per cap"
).encode(x="policy_years", y=alt.Y("MME_per_cap", title="Opioid per Cap", scale=alt.Scale(zero=False)), color=alt.Color('fl:N', scale=scale, title=''))

base = before.transform_regression("policy_years", "MME_per_cap").mark_line()

after = alt.Chart(
    fl_opi_after, title="Difference in Difference: Florida vs. Control, Opioids per cap"
).encode(x="policy_years", y="MME_per_cap", color=alt.Color('control:N', scale=scale, title=''))

fl_chart_opioid = (
    base + base2 + before_line + before_line2 + after_line + after_line2 + sep_line
)

fl_chart_opioid

alt.LayerChart(...)

In [71]:
# Creating florida deathd df
opioid_deaths_fl=opioid_deaths[opioid_deaths["STNAME"]=="Florida"]
opioid_deaths_fl["policy_years"]= opioid_deaths_fl["Year"]-2010

fl_death_before=opioid_deaths_fl[opioid_deaths_fl["policy_years"]<0]
fl_death_after=opioid_deaths_fl[opioid_deaths_fl["policy_years"]>=0]

/var/folders/g3/gw7r7tvj63j5wjhsmmnq03qr0000gn/T/ipykernel_39162/1757448420.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opioid_deaths_fl["policy_years"]= opioid_deaths_fl["Year"]-2010


In [72]:
# florida deaths pre/post plot
before = alt.Chart(
    fl_death_before, title="Pre-Post Policy: Florida, Overdose Deaths per cap"
).encode(x="policy_years", y=alt.Y("deaths_per_cap", title="Deaths per Cap", scale=alt.Scale(zero=False)), color=alt.Color('fl:N', scale=scale, title=''))

base = before.transform_regression("policy_years", "deaths_per_cap").mark_line()

fit, before_line = get_reg_fit(
    fl_death_before, yvar="deaths_per_cap", xvar="policy_years", alpha=0.05, col="red"
)
fit, after_line = get_reg_fit(
    fl_death_after, yvar="deaths_per_cap", xvar="policy_years", alpha=0.05, col="red"
)

fl_chart_death = base + before_line + after_line + sep_line
fl_chart_death

alt.LayerChart(...)

In [74]:
# Creating control dataframes
states = ["SC","AL","GA","MS"]
states2 = ["South Carolina","Alabama","Georgia","Mississippi"]

opioid_buyers_con=opioid_buyers[opioid_buyers["BUYER_STATE"].isin(states)]
opioid_buyers_con.sample(10)
opioid_buyers_con["policy_years"]= opioid_buyers_con["year"]-2010

con_opi_before=opioid_buyers_con[opioid_buyers_con["policy_years"]<0]
con_opi_after=opioid_buyers_con[opioid_buyers_con["policy_years"]>=0]


opioid_deaths_con=opioid_deaths[opioid_deaths["STNAME"].isin(states2)]
opioid_deaths_con["policy_years"]= opioid_deaths_con["Year"]-2010


con_death_before=opioid_deaths_con[opioid_deaths_con["policy_years"]<0]
con_death_after=opioid_deaths_con[opioid_deaths_con["policy_years"]>=0]

/var/folders/g3/gw7r7tvj63j5wjhsmmnq03qr0000gn/T/ipykernel_39162/4233447948.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opioid_buyers_con["policy_years"]= opioid_buyers_con["year"]-2010
/var/folders/g3/gw7r7tvj63j5wjhsmmnq03qr0000gn/T/ipykernel_39162/4233447948.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opioid_deaths_con["policy_years"]= opioid_deaths_con["Year"]-2010


In [75]:
#Difference in difference plot, deaths, FL vs control
fit, before_line = get_reg_fit(
    con_death_before, yvar="deaths_per_cap", xvar="policy_years", alpha=0.05, col="blue"
)

fit, after_line = get_reg_fit(
    con_death_after, yvar="deaths_per_cap", xvar="policy_years", alpha=0.05, col="blue"
)

before = alt.Chart(
    con_death_before,
    title="Difference in Difference: Florida vs. Control, Overdose Deaths per cap",
).encode(x="policy_years", y=alt.Y("deaths_per_cap", title="Deaths per Cap", scale=alt.Scale(zero=False)), color=alt.Color('fl:N', scale=scale, title=''))

base = before.transform_regression("policy_years", "deaths_per_cap").mark_line(
    color="#FFAA00"
)

con_chart_death = base + before_line + after_line + sep_line
diff_fl_death=con_chart_death+fl_chart_death+sep_line
diff_fl_death

alt.LayerChart(...)

# Texas Plots

In [76]:
# creating texas dataframes
opioid_deaths_tx=opioid_deaths[opioid_deaths["STNAME"]=="Texas"]
opioid_deaths_tx["policy_years"]= opioid_deaths_tx["Year"]-2007

tx_death_before=opioid_deaths_tx[opioid_deaths_tx["policy_years"]<0]
tx_death_after=opioid_deaths_tx[opioid_deaths_tx["policy_years"]>=0]

/var/folders/g3/gw7r7tvj63j5wjhsmmnq03qr0000gn/T/ipykernel_39162/3397412376.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opioid_deaths_tx["policy_years"]= opioid_deaths_tx["Year"]-2007


In [77]:
# Creating texas control dataframes
states = ["Oklahoma","Lousiana","New Mexico"]

opioid_deaths_con=opioid_deaths[opioid_deaths["STNAME"].isin(states)]
opioid_deaths_con["policy_years"]= opioid_deaths_con["Year"]-2007

con_death_before=opioid_deaths_con[opioid_deaths_con["policy_years"]<0]
con_death_after=opioid_deaths_con[opioid_deaths_con["policy_years"]>=0]

/var/folders/g3/gw7r7tvj63j5wjhsmmnq03qr0000gn/T/ipykernel_39162/2791965605.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opioid_deaths_con["policy_years"]= opioid_deaths_con["Year"]-2007


In [78]:
# texas deaths pre/post plot
# Stuffs for making legend
legend = alt.Chart(fl_opi_before).transform_calculate(tx="'Texas'", control="'control'")

scale = alt.Scale(domain=["Texas", "Control"], range=["red", "blue"])
before = alt.Chart(
    tx_death_before, title="Pre-Post Policy: Texas, Overdose Deaths per cap"
).encode(
    x="policy_years",
    y=alt.Y("deaths_per_cap", title="Deaths per Cap", scale=alt.Scale(zero=False)),
    color=alt.Color("tx:N", scale=scale, title=""),
)
base = before.transform_regression(
    "policy_years",
    "deaths_per_cap",
).mark_line()

fit, before_line = get_reg_fit(
    tx_death_before, yvar="deaths_per_cap", xvar="policy_years", alpha=0.05, col="red"
)
fit, after_line = get_reg_fit(
    tx_death_after, yvar="deaths_per_cap", xvar="policy_years", alpha=0.05, col="red"
)

tx_chart_death = base + before_line + after_line + sep_line
tx_chart_death


alt.LayerChart(...)

In [79]:
# diff-in-diff
fit, before_line = get_reg_fit(
    con_death_before, yvar="deaths_per_cap", xvar="policy_years", alpha=0.05
)
fit, after_line = get_reg_fit(
    con_death_after, yvar="deaths_per_cap", xvar="policy_years", alpha=0.05
)

before = alt.Chart(
    con_death_before,
    title="Difference in Difference: Texas vs. Control, Overdose Deaths per cap",
).encode(
    x="policy_years",
    y=alt.Y("deaths_per_cap", title="Deaths per Cap", scale=alt.Scale(zero=False)),
    color=alt.Color("tx:N", scale=scale, title=""),
)

base = before.transform_regression("policy_years", "deaths_per_cap").mark_line(
    color="#FFAA00"
)
con_chart_death = base + before_line + after_line + sep_line
diff_tx_death = con_chart_death + tx_chart_death + sep_line
diff_tx_death


alt.LayerChart(...)

# Washington Plots

In [80]:
# Creating Washington buyers df
states = ["ID","OR","MT", "WA"]
opioid_buyers_wa=opioid_buyers[opioid_buyers["BUYER_STATE"].isin(states)]

#create column, to indicate whether control or not (1 for control, 0 for Washington)
opioid_buyers_wa["is_control"]=np.where(opioid_buyers_wa["BUYER_STATE"]== 'WA', 0, 1)

#create policy years 
opioid_buyers_wa["policy_years"]= opioid_buyers_wa["year"]-2012
wa_opi_before=opioid_buyers_wa[opioid_buyers_wa["policy_years"]<0]
wa_opi_after=opioid_buyers_wa[opioid_buyers_wa["policy_years"]>=0]

/var/folders/g3/gw7r7tvj63j5wjhsmmnq03qr0000gn/T/ipykernel_39162/2992522382.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opioid_buyers_wa["is_control"]=np.where(opioid_buyers_wa["BUYER_STATE"]== 'WA', 0, 1)
/var/folders/g3/gw7r7tvj63j5wjhsmmnq03qr0000gn/T/ipykernel_39162/2992522382.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opioid_buyers_wa["policy_years"]= opioid_buyers_wa["year"]-2012


In [81]:
# Washington buyers pre/post plot
# Stuffs for making legends
legend = alt.Chart(wa_opi_before).transform_calculate(
    fl="'Washington'", control="'control'"
)
scale = alt.Scale(domain=["Washington", "Control"], range=["red", "blue"])

before = alt.Chart(
    wa_opi_before, title="Pre-Post Policy: Washington, Opioids per cap"
).encode(
    x="policy_years",
    y=alt.Y("MME_per_cap", title="Opioids per Cap", scale=alt.Scale(zero=False)),
    color=alt.Color("fl:N", scale=scale, title=""),
)
base = before.transform_regression("policy_years", "MME_per_cap").mark_line()
after = alt.Chart(
    wa_opi_after, title="Pre-Post Policy: Washington, Opioids per cap"
).encode(
    x="policy_years",
    y="MME_per_cap",
    color=alt.Color("control:N", scale=scale, title=""),
)
base2 = after.transform_regression("policy_years", "MME_per_cap").mark_line()

fit, before_line = get_reg_fit(
    wa_opi_before[wa_opi_before["is_control"] == 1],
    yvar="MME_per_cap",
    xvar="policy_years",
    alpha=0.05,
    col="blue",
)
fit, before_line2 = get_reg_fit(
    wa_opi_before[wa_opi_before["is_control"] == 0],
    yvar="MME_per_cap",
    xvar="policy_years",
    alpha=0.05,
    col="red",
)
fit, after_line = get_reg_fit(
    wa_opi_after[wa_opi_after["is_control"] == 1],
    yvar="MME_per_cap",
    xvar="policy_years",
    alpha=0.05,
    col="blue",
)
fit, after_line2 = get_reg_fit(
    wa_opi_after[wa_opi_after["is_control"] == 0],
    yvar="MME_per_cap",
    xvar="policy_years",
    alpha=0.05,
    col="red",
)

wa_pre_post = base + before_line2 + after_line2 + sep_line
wa_pre_post


alt.LayerChart(...)

In [82]:
# diff-in-diff
before = alt.Chart(
    wa_opi_before,
    title="Difference in Difference: Washington vs. Control, Opioids per cap",
).encode(
    x="policy_years",
    y=alt.Y("MME_per_cap", title="Opioid per Cap", scale=alt.Scale(zero=False)),
    color=alt.Color("fl:N", scale=scale, title=""),
)

base = before.transform_regression("policy_years", "MME_per_cap").mark_line()

after = alt.Chart(
    wa_opi_after,
    title="Difference in Difference: Washington vs. Control, Opioids per cap",
).encode(
    x="policy_years",
    y="MME_per_cap",
    color=alt.Color("control:N", scale=scale, title=""),
)

wa_chart_opioid = (
    base + base2 + before_line + before_line2 + after_line + after_line2 + sep_line
)

wa_chart_opioid


alt.LayerChart(...)

In [83]:
# creating Washington dataframes
opioid_deaths_wa=opioid_deaths[opioid_deaths["STNAME"]=="Washington"]
opioid_deaths_wa["policy_years"]= opioid_deaths_wa["Year"]-2012

wa_death_before=opioid_deaths_wa[opioid_deaths_wa["policy_years"]<0]
wa_death_after=opioid_deaths_wa[opioid_deaths_wa["policy_years"]>=0]

/var/folders/g3/gw7r7tvj63j5wjhsmmnq03qr0000gn/T/ipykernel_39162/3859497698.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opioid_deaths_wa["policy_years"]= opioid_deaths_wa["Year"]-2012


In [84]:
# Creating wa control dataframes
states = ["Idaho","Oregon","Montana"]

opioid_deaths_con=opioid_deaths[opioid_deaths["STNAME"].isin(states)]
opioid_deaths_con["policy_years"]= opioid_deaths_con["Year"]-2012

con_death_before=opioid_deaths_con[opioid_deaths_con["policy_years"]<0]
con_death_after=opioid_deaths_con[opioid_deaths_con["policy_years"]>=0]

/var/folders/g3/gw7r7tvj63j5wjhsmmnq03qr0000gn/T/ipykernel_39162/3330578384.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  opioid_deaths_con["policy_years"]= opioid_deaths_con["Year"]-2012


In [85]:
# washington deaths pre/post plot
# Stuffs for making legend
legend = alt.Chart(fl_opi_before).transform_calculate(
    wa="'Washington'", control="'control'"
)

scale = alt.Scale(domain=["Washington", "Control"], range=["red", "blue"])
before = alt.Chart(
    wa_death_before, title="Pre-Post Policy: Washington, Overdose Deaths per cap"
).encode(
    x="policy_years",
    y=alt.Y("deaths_per_cap", title="Deaths per Cap", scale=alt.Scale(zero=False)),
    color=alt.Color("wa:N", scale=scale, title=""),
)
base = before.transform_regression("policy_years", "deaths_per_cap").mark_line()

fit, before_line = get_reg_fit(
    wa_death_before, yvar="deaths_per_cap", xvar="policy_years", alpha=0.05, col="red"
)
fit, after_line = get_reg_fit(
    wa_death_after, yvar="deaths_per_cap", xvar="policy_years", alpha=0.05, col="red"
)

wa_chart_death = base + before_line + after_line + sep_line
wa_chart_death


alt.LayerChart(...)

In [86]:
# diff-in-diff
fit, before_line = get_reg_fit(
    con_death_before, yvar="deaths_per_cap", xvar="policy_years", alpha=0.05
)
fit, after_line = get_reg_fit(
    con_death_after, yvar="deaths_per_cap", xvar="policy_years", alpha=0.05
)

before = alt.Chart(
    con_death_before,
    title="Difference in Difference: Washington vs. Control, Overdose Deaths per cap",
).encode(
    x="policy_years",
    y=alt.Y("deaths_per_cap", title="Deaths per Cap", scale=alt.Scale(zero=False)),
    color=alt.Color("wa:N", scale=scale, title=""),
)

base = before.transform_regression("policy_years", "deaths_per_cap").mark_line(
    color="#FFAA00"
)

con_chart_death = base + before_line + after_line + sep_line
diff_wa_death = con_chart_death + wa_chart_death + sep_line
diff_wa_death


alt.LayerChart(...)

## Texas Monthly Plot

In [87]:
month_opioid_buyers = pd.read_parquet("/Users/yangshining/Desktop/pds2021-opioids-pds6/10_modified_data/opi_tx_pop.parquet", engine='fastparquet')

month_opioid_buyers=month_opioid_buyers.rename(columns={"MME per cap":"MME_per_cap"})
month_opioid_buyers.sample(10)

BUYER_STATE BUYER_COUNTY  year  month           MME  Population  \
index                                                                   
21853          TX     CHEROKEE  2007      8  1.115175e+06       49669   
28414          TX     HEMPHILL  2013      5  8.249528e+04        4153   
25209          TX      FAYETTE  2006      1  2.226454e+04       23631   
15103          OK    MCCURTAIN  2011      2  1.144938e+06       33309   
27797          TX       HARDIN  2006     11  1.089143e+06       51470   
1632           LA       DESOTO  2013      3  3.836609e+05       27089   
25768          TX     FRANKLIN  2008      2  2.028311e+05       10604   
14408          OK        LOGAN  2007      3  6.389752e+05       38709   
7576           NM     DONA ANA  2013     10  6.065401e+06      214288   
28370          TX     HEMPHILL  2009      8  5.148330e+04        3802   

       MME_per_cap  
index               
21853    22.452129  
28414    19.864020  
25209     0.942175  
15103    34.373232  
27797    21.160741  
1632     14.162977  
25768    19.127787  
14408    16.507148  
7576     28.304905  
28370    13.541110

In [6]:
month_opioid_buyers['BUYER_STATE'].unique()

array(['LA', 'NM', 'OK', 'TX'], dtype=object)

In [4]:
month_opioid_buyers['year'].unique()

array([2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014])

In [5]:
month_opioid_buyers['month'].unique()

array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12])

In [88]:
opioid_buyers_tx=month_opioid_buyers.copy()

#create column, to indicate whether control or not (1 for control, 0 for Texas)
opioid_buyers_tx["is_control"]=np.where(opioid_buyers_tx["BUYER_STATE"]== 'TX', 0, 1)

# add date = year + month
opioid_buyers_tx['date'] = opioid_buyers_tx['month'].map(str)+ '-' + opioid_buyers_tx['year'].map(str)
opioid_buyers_tx['date'] = pd.to_datetime(opioid_buyers_tx['date'], format='%m-%Y').dt.strftime('%m-%Y')

# The policy in Texas came into effect in Jan, 2007

#create policy years 
opioid_buyers_tx["policy_years"]= opioid_buyers_tx["year"]-2007

# add policy months
opioid_buyers_tx['policy_months'] = (opioid_buyers_tx['year']-2007)*12 + (opioid_buyers_tx['month']-1)

tx_opi_before=opioid_buyers_tx[opioid_buyers_tx["policy_months"]<0]

tx_opi_after=opioid_buyers_tx[opioid_buyers_tx["policy_months"]>=0]

In [27]:
tx_opi_before['BUYER_STATE'].unique()

array(['LA', 'NM', 'OK', 'TX'], dtype=object)

In [28]:
tx_opi_before

BUYER_STATE BUYER_COUNTY  year  month           MME  Population  \
index                                                                   
0              LA       ACADIA  2006      1  2.821391e+05       60522   
1              LA       ACADIA  2006      2  1.607831e+06       60522   
2              LA       ACADIA  2006      3  1.971931e+06       60522   
3              LA       ACADIA  2006      4  1.578223e+06       60522   
4              LA       ACADIA  2006      5  1.914167e+06       60522   
...           ...          ...   ...    ...           ...         ...   
42223          TX       ZAVALA  2006      8  5.282115e+04       11642   
42224          TX       ZAVALA  2006      9  7.431285e+04       11642   
42225          TX       ZAVALA  2006     10  7.885335e+04       11642   
42226          TX       ZAVALA  2006     11  7.037775e+04       11642   
42227          TX       ZAVALA  2006     12  5.536383e+04       11642   

       MME_per_cap  is_control     date  policy_years  policy_months  
index                                                                 
0         4.661761           1  01-2006            -1            -12  
1        26.566053           1  02-2006            -1            -11  
2        32.582050           1  03-2006            -1            -10  
3        26.076841           1  04-2006            -1             -9  
4        31.627626           1  05-2006            -1             -8  
...            ...         ...      ...           ...            ...  
42223     4.537120           0  08-2006            -1             -5  
42224     6.383169           0  09-2006            -1             -4  
42225     6.773179           0  10-2006            -1             -3  
42226     6.045160           0  11-2006            -1             -2  
42227     4.755526           0  12-2006            -1             -1  

[4717 rows x 11 columns]

In [89]:
## Nick's code for confidence bands 
def get_reg_fit2(data, yvar, xvar, alpha=0.05,col="blue"):
    import statsmodels.formula.api as smf

    # Grid for predicted values
    x = data.loc[pd.notnull(data[yvar]), xvar]
    print(f'yvar : {yvar}, xvar : {xvar}, x = {x}')
    xmin = x.min()
    xmax = x.max()
    step = (xmax - xmin) / 100
    print(f'xmin : {xmin}, xmax : {xmax}, step = {step}')
    grid = np.arange(xmin, xmax + step, step)
    predictions = pd.DataFrame({xvar: grid})

    # Fit model, get predictions
    model = smf.ols(f"{yvar} ~ {xvar}", data=data).fit()
    model_predict = model.get_prediction(predictions[xvar])
    predictions[yvar] = model_predict.summary_frame()["mean"]
    predictions[["ci_low", "ci_high"]] = model_predict.conf_int(alpha=alpha)

    # Build chart
    reg = alt.Chart(predictions).mark_line(color=col).encode(
        x=alt.X(xvar, axis=alt.Axis(title='Months from Policy Change')),
        y=alt.X(yvar, axis=alt.Axis(title='')))
    ci = (
        alt.Chart(predictions)
        .mark_errorband(color=col)
        .encode(
            x=xvar,
            y=alt.Y("ci_low", title=""),
            y2="ci_high",
        )
    )
    chart = ci + reg
    return predictions, chart

In [90]:
#create vertical line for plots
data = pd.DataFrame({"a": [0]})
sep_line = (alt.Chart(data).mark_rule(color="black", strokeDash=[10, 10]).encode(x=alt.X("a:Q", title="")))

In [91]:
# Texas buyers pre/post plot

# Stuffs for making legends

legend = alt.Chart(tx_opi_before).transform_calculate(tx= "'Texas'", control="'control'")

scale = alt.Scale(domain=["Texas", "Control"], range=['red', 'blue'])

before = alt.Chart(
    tx_opi_before, title="Pre-Post Policy: Texas, Opioids per cap"
).encode(x="policy_months", y=alt.Y("MME_per_cap", title="Opioids per Cap", scale=alt.Scale(zero=False)), color=alt.Color('tx:N', scale=scale, title=''))

base = before.transform_regression("policy_months", "MME_per_cap").mark_line()

after = alt.Chart(
    tx_opi_after, title="Pre-Post Policy: Texas, Opioids per cap"
).encode(x="policy_months", y="MME_per_cap", color=alt.Color('control:N', scale=scale, title=''))

base2 = after.transform_regression("policy_months", "MME_per_cap").mark_line()

fit, before_line = get_reg_fit2(
    tx_opi_before[tx_opi_before["is_control"] == 1],
    yvar="MME_per_cap",
    xvar="policy_months",
    alpha=0.05,
    col="blue",
)
fit, before_line2 = get_reg_fit2(
    tx_opi_before[tx_opi_before["is_control"] == 0],
    yvar="MME_per_cap",
    xvar="policy_months",
    alpha=0.05,
    col="red"
)
fit, after_line = get_reg_fit2(
    tx_opi_after[tx_opi_after["is_control"] == 1],
    yvar="MME_per_cap",
    xvar="policy_months",
    alpha=0.05,
    col="blue",
)
fit, after_line2 = get_reg_fit2(
    tx_opi_after[tx_opi_after["is_control"] == 0],
    yvar="MME_per_cap",
    xvar="policy_months",
    alpha=0.05,
    col="red"
)

tx_opi_pre_post = base + before_line2 + after_line2 + sep_line
tx_opi_pre_post

yvar : MME_per_cap, xvar : policy_months, x = index
0       -12
1       -11
2       -10
3        -9
4        -8
         ..
18181    -5
18182    -4
18183    -3
18184    -2
18185    -1
Name: policy_months, Length: 2035, dtype: int64
xmin : -12, xmax : -1, step = 0.11
yvar : MME_per_cap, xvar : policy_months, x = index
18282   -12
18283   -11
18284   -10
18285    -9
18286    -8
         ..
42223    -5
42224    -4
42225    -3
42226    -2
42227    -1
Name: policy_months, Length: 2682, dtype: int64
xmin : -12, xmax : -1, step = 0.11
yvar : MME_per_cap, xvar : policy_months, x = index
12        0
13        1
14        2
15        3
16        4
         ..
18277    91
18278    92
18279    93
18280    94
18281    95
Name: policy_months, Length: 16247, dtype: int64
xmin : 0, xmax : 95, step = 0.95
yvar : MME_per_cap, xvar : policy_months, x = index
18294     0
18295     1
18296     2
18297     3
18298     4
         ..
42319    91
42320    92
42321    93
42322    94
42323    95
Name: policy_mon

alt.LayerChart(...)

## Diff-in-Diff for opioid, TX and control

In [92]:
# diff-in-diff

before = alt.Chart(
    tx_opi_before, title="Difference in Difference: Texas vs. Control, Opioids per cap"
).encode(
    x="policy_months",
    y=alt.Y("MME_per_cap", title="Opioid per Cap", scale=alt.Scale(zero=False)),
    color=alt.Color("tx:N", scale=scale, title=""),
)


base = before.transform_regression("policy_months", "MME_per_cap").mark_line()


after = alt.Chart(
    tx_opi_after, title="Difference in Difference: Texas vs. Control, Opioids per cap"
).encode(
    x="policy_months",
    y="MME_per_cap",
    color=alt.Color("control:N", scale=scale, title=""),
)

base2 = after.transform_regression("policy_months", "MME_per_cap").mark_line()

tx_chart_opioid = (
    base  +  before_line + before_line2 + after_line + after_line2 + sep_line
)


tx_chart_opioid


alt.LayerChart(...)